# Lecture 7 DPA Lab - High Data Complexity Power/EM 1
### In this example we will find a byte from the key of AES (with key size of 16) algorithm.
#### This notebook is based on the example presented in the class

##### Prerequisits

In [2]:
#Resources and Dependencies, if you are interested, you can use the links to see the code
!wget https://raw.githubusercontent.com/Yossioren/AttacksonImplementationsCourseBook/master/Labs/WS2.mat
!wget https://raw.githubusercontent.com/Yossioren/AttacksonImplementationsCourseBook/master/Labs/hamming_weight.py
!wget https://raw.githubusercontent.com/Yossioren/AttacksonImplementationsCourseBook/master/Labs/aes_lib.py
!pip install -q bokeh

--2021-07-18 18:09:05--  https://raw.githubusercontent.com/Yossioren/AttacksonImplementationsCourseBook/master/Labs/WS2.mat
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.108.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 40004112 (38M) [application/octet-stream]
Saving to: ‘WS2.mat’

WS2.mat             100%[===================>]  38.15M  43.0MB/s    in 0.9s    

2021-07-18 18:09:06 (43.0 MB/s) - ‘WS2.mat’ saved [40004112/40004112]

--2021-07-18 18:09:06--  https://raw.githubusercontent.com/Yossioren/AttacksonImplementationsCourseBook/master/Labs/hamming_weight.py
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.109.133, 185.199.111.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.109.133|:443... connected.
HTTP request sent, aw

In [1]:
import matplotlib.pyplot as plt
import numpy as np
import scipy.io as sp
from hamming_weight import hamming_weight
from bokeh.models import Range1d
from aes_lib import aes_crypt_8bit_and_leak, aes_sbox

from bokeh.plotting import figure, show
from bokeh.models import Range1d, ColorBar, LinearColorMapper, BasicTicker
from bokeh.io import output_notebook
import bokeh.colors.named as bokeh_colors_names

bokeh_colors_names_arr = dir(bokeh_colors_names)[10:]
bokeh_colors_names_arr = bokeh_colors_names_arr*3

# Call once to configure Bokeh to display plots inline in the notebook.
output_notebook()

##### A helper function for getting a heatmap

In [2]:
def getHeatMap(title, xaxis, yaxis, data, dh, dw):
    indMax = np.unravel_index(np.argmax(data, axis=None), data.shape)
    print(np.shape(data), data[indMax])    
    color_mapper = LinearColorMapper(palette="Turbo256", low=1e-2, high=data[indMax])
    # Log heatmap

    fig = figure(title=title, x_range=(0,dw), y_range=(0,dh), x_axis_label=xaxis, y_axis_label=yaxis,
        tooltips=[("x", "$x"), ("y", "$y"), ("value", "@image")], plot_height=700, plot_width=700)
    fig.image(image=[data], x=0, y=0, dw=dw, dh=dh, color_mapper=color_mapper, level="image")
    # Palette values-https://docs.bokeh.org/en/latest/docs/reference/palettes.html

    # Add heat map
    color_bar = ColorBar(color_mapper=color_mapper, ticker=BasicTicker(), border_line_color=None, location=(0,0))
    fig.add_layout(color_bar, 'right')

    return fig

##### Load the traces and inputs data

Globals

In [3]:
DPA = 0
CPA = 1
DPA_OR_CPA = CPA  # DPA
key_bytes_to_guess = [5,6]  # We want to guess one byte in the key, which is located in index number 5
correct_key_time = dict()  # Save for each guess the key and the time

Make sure the matlab AES scripts are in the path,  
Load WS2, show a few traces

In [4]:
ws2 = sp.loadmat('WS2.mat')
print(np.shape(ws2['traces']))  # D = 200, T = 100000
ws2

(200, 100000)


{'SubBytes': array([[ 99, 124, 119, 123, 242, 107, 111, 197,  48,   1, 103,  43, 254,
         215, 171, 118, 202, 130, 201, 125, 250,  89,  71, 240, 173, 212,
         162, 175, 156, 164, 114, 192, 183, 253, 147,  38,  54,  63, 247,
         204,  52, 165, 229, 241, 113, 216,  49,  21,   4, 199,  35, 195,
          24, 150,   5, 154,   7,  18, 128, 226, 235,  39, 178, 117,   9,
         131,  44,  26,  27, 110,  90, 160,  82,  59, 214, 179,  41, 227,
          47, 132,  83, 209,   0, 237,  32, 252, 177,  91, 106, 203, 190,
          57,  74,  76,  88, 207, 208, 239, 170, 251,  67,  77,  51, 133,
          69, 249,   2, 127,  80,  60, 159, 168,  81, 163,  64, 143, 146,
         157,  56, 245, 188, 182, 218,  33,  16, 255, 243, 210, 205,  12,
          19, 236,  95, 151,  68,  23, 196, 167, 126,  61, 100,  93,  25,
         115,  96, 129,  79, 220,  34,  42, 144, 136,  70, 238, 184,  20,
         222,  94,  11, 219, 224,  50,  58,  10,  73,   6,  36,  92, 194,
         211, 172,  98, 14

Shrink it a little so it runs faster

In [5]:
traces = ws2['traces'][:, 0:30000]
input_count = np.shape(traces)[0]
trace_length = np.shape(traces)[1]

##### Plot two traces for an example

In [6]:
p = figure(title='Traces of AES computation', x_axis_label='Time (ms)', y_axis_label='value', tooltips=[("x", "$x"), ("y", "$y")])
times = np.linspace(0,len(traces[0, :]), len(traces[0, :]))
p.x_range=Range1d(300, 500)
p.line(times, traces[0, :], legend_label='Trace 1', line_color='blue')
p.line(times, traces[1, :], legend_label='Trace 2', line_color='orange')
show(p)

##### Initialize classification vectors before the key guessing process

In [15]:
classification_outputs = [np.zeros(shape=(2**8, trace_length)) for i in range(16)]
print(np.shape(classification_outputs[0]))
# #
#  For each key guess
trace_classifications = [np.zeros(shape=(2**8, input_count)) for i in range(16)]
inputs = ws2['inputs']

(256, 30000)


In [16]:
print(np.shape(traces), np.shape(classification_outputs), np.shape(trace_classifications))

(200, 30000) (16, 256, 30000) (16, 256, 200)


##### Guessing the byte of the key and finding the correct guess with Vaizata

In [17]:
for key_byte_to_guess in key_bytes_to_guess:
  classification_output = classification_outputs[key_byte_to_guess]
  trace_classification = trace_classifications[key_byte_to_guess]

  print(f'index {key_byte_to_guess}:')

  for key_guess in range(2**8):
    # For each plaintext input
    for input in range(input_count):
      # Calculate what the value of S[P ^ K] is
      p_xor_k = np.bitwise_xor(inputs[input, key_byte_to_guess - 1], key_guess)
      s_p_xor_k = aes_sbox(p_xor_k, 1)

      if DPA_OR_CPA == DPA:
        trace_classification[key_guess, input] = (np.bitwise_and(s_p_xor_k, 1) != 0)
      else:
        trace_classification[key_guess, input] = hamming_weight(s_p_xor_k)

    # % Calculate the mean of each classified set
    if DPA_OR_CPA == DPA:
      mean_for_1 = np.mean(traces[trace_classification[key_guess, :] == 1, :], axis=0)
      mean_for_0 = np.mean(traces[trace_classification[key_guess, :] == 0, :], axis=0)
      # % Save the difference of means in the table
      classification_output[key_guess, :] = np.subtract(mean_for_1, mean_for_0)
    else:
      shape = np.shape(trace_classification[key_guess, :])
      my_trace = np.reshape(trace_classification[key_guess, :], newshape=(shape[0], 1))

      traces1 = (traces - traces.mean(axis=0))/traces.std(axis=0)  # A matrix
      my_trace = (my_trace - my_trace.mean(axis=0))/my_trace.std(axis=0)  # B matrix
      correlation = (np.dot(my_trace.T, traces1) / my_trace.shape[0])[0]

      classification_output[key_guess, :] = np.transpose(correlation)

      print('[{:02x}]'.format(key_guess), end=" ")
      if (key_guess % 16) == 15:
        print('\n')

  # Find out the correct time and correct key
  absolute = np.abs(classification_output)
  index = np.unravel_index(np.argmax(absolute, axis=None), absolute.shape)
  correct_time = index[1]
  absolute = np.abs(classification_output[:, correct_time])
  correct_key = np.argmax(absolute)  # this is actually correct_key + 1
  correct_key_time[key_byte_to_guess] = (correct_key, correct_time)
  print(f'Key index {key_byte_to_guess}: correct_key={correct_key}, correct_time={correct_time}')

index 5:
[00] [01] [02] [03] [04] [05] [06] [07] [08] [09] [0a] [0b] [0c] [0d] [0e] [0f] 

[10] [11] [12] [13] [14] [15] [16] [17] [18] [19] [1a] [1b] [1c] [1d] [1e] [1f] 

[20] [21] [22] [23] [24] [25] [26] [27] [28] [29] [2a] [2b] [2c] [2d] [2e] [2f] 

[30] [31] [32] [33] [34] [35] [36] [37] [38] [39] [3a] [3b] [3c] [3d] [3e] [3f] 

[40] [41] [42] [43] [44] [45] [46] [47] [48] [49] [4a] [4b] [4c] [4d] [4e] [4f] 

[50] [51] [52] [53] [54] [55] [56] [57] [58] [59] [5a] [5b] [5c] [5d] [5e] [5f] 

[60] [61] [62] [63] [64] [65] [66] [67] [68] [69] [6a] [6b] [6c] [6d] [6e] [6f] 

[70] [71] [72] [73] [74] [75] [76] [77] [78] [79] [7a] [7b] [7c] [7d] [7e] [7f] 

[80] [81] [82] [83] [84] [85] [86] [87] [88] [89] [8a] [8b] [8c] [8d] [8e] [8f] 

[90] [91] [92] [93] [94] [95] [96] [97] [98] [99] [9a] [9b] [9c] [9d] [9e] [9f] 

[a0] [a1] [a2] [a3] [a4] [a5] [a6] [a7] [a8] [a9] [aa] [ab] [ac] [ad] [ae] [af] 

[b0] [b1] [b2] [b3] [b4] [b5] [b6] [b7] [b8] [b9] [ba] [bb] [bc] [bd] [be] [bf] 

[c0] [c

#### For analyzing a specific index from the key, please initialize the key_index below

In [32]:
key_byte_to_guess = key_bytes_to_guess[0] # *Change* for another indexes, default is the first index from the indexes array
trace_classification = trace_classifications[key_byte_to_guess]
classification_output = classification_outputs[key_byte_to_guess]
correct_key, correct_time = correct_key_time[key_byte_to_guess]

##### Plot the trace classification matrix

In [33]:
[dh, dw] = np.shape(trace_classification)

show(getHeatMap('Trace classification', 'Trace index', 'Key guess for byte  ' + str(key_byte_to_guess), trace_classification, dh, dw))

(256, 200) 8.0


##### Show some more statistics

In [34]:
heights = np.abs(classification_output[:, correct_time])
p = figure(title='Correlation for each value of the byte', x_axis_label='Key guess', y_axis_label='Correlation', tooltips=[("x", "$x"), ("y", "$y")])
p.vbar(x=range(1, np.shape(classification_output)[0] + 1), top=heights, width=0.8, fill_color='blue')
show(p)

###### CPA only: show the actual power consumption at correct time, compared to power model

In [35]:
plot1 = np.true_divide(traces[:, correct_time], 5)
p = figure(title='The actual power consumption at correct time compared to the power model', x_axis_label='Trace index', y_axis_label='power', tooltips=[("x", "$x"), ("y", "$y")])
times = np.linspace(0,200,200)
p.line(times, plot1, legend_label='Power model for correct key', line_color='blue')
p.line(times, np.transpose(trace_classification[correct_key, :]), legend_label='Power consumption at correct time', line_color='orange')
show(p)

In [36]:
window_frame = 100#ms
offframe = 2*window_frame
ys=[x[correct_time - offframe:correct_time + offframe] for x in classification_output]
p = figure(title='The correct key at the correct time', x_axis_label='Time (ms)', y_axis_label='Correlation', tooltips=[("x", "$x"), ("y", "$y"), ("Key guess", "$index")])
times = np.linspace(correct_time - offframe, correct_time + offframe, offframe*2)
times = np.tile(times,(len(ys),1))#duplicate the array for the multiline function
p.multi_line(xs=list(times), ys=ys, color=bokeh_colors_names_arr[:len(times)])
#p.multi_line(xs=[[1, 2, 3], [2, 3, 4]], ys=[[6, 7, 2], [4, 5, 7]], color=['red','green'])
p.x_range=Range1d(correct_time - window_frame, correct_time + window_frame)
show(p)

In [37]:
p = figure(title='Correlation at the correct time', x_axis_label='Time (ms)', y_axis_label='Correlation', tooltips=[("x", "$x"), ("y", "$y")])
times = np.linspace(0,trace_length,len(classification_output[correct_key, :]))
p.line(times, classification_output[correct_key, :], line_color='blue')
show(p)